In [69]:
from imutils import paths
import cv2
import numpy as np
import os
import pandas as pd
import sys
from PIL import Image
from matplotlib import pyplot as plt
from tqdm import tqdm
import plotly.express as px
%matplotlib inline

In [20]:
def blur(image):
	# compute the Laplacian of the image and then return the focus
	# measure, which is simply the variance of the Laplacian
	return cv2.Laplacian(image, cv2.CV_64F).var()

In [66]:
def blur_avg(imgdata):
    image = cv2.imread(imgdata['path'])
    original = image.copy()
    gray = cv2.blur(cv2.cvtColor(image, cv2.COLOR_BGR2GRAY),(7,7))
#     print(imgdata['name'])
    blurs = []
# Different threshold conditions for different diameters
    if imgdata['dia'] == 400:
        thresh = cv2.threshold(gray, 0, 255, cv2.THRESH_BINARY_INV + cv2.THRESH_OTSU)[1]
    else:
        thresh = cv2.threshold(gray, 138, 255, cv2.THRESH_BINARY_INV)[1]

# Find contours, obtain bounding box, extract and save ROI
    cnts = cv2.findContours(thresh, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    cnts = cnts[0] if len(cnts) == 2 else cnts[1]

# Creating bounding boxes for the detected countours, creating 256 x 256 crops of the ROIs
    ROI_number = 0
    for cnt in cnts:
#         if not cv2.isContourConvex(cnt):
#             continue
        x,y,w,h = cv2.boundingRect(cnt)
        # Rejecting ROIs that are not roughly square shaped to avoid low-quality training data
        if w/h > 0.9 and w/h < 1.1 and w*h > 2500:
            
            # Drawing rectangle around ROI
#             image = cv2.rectangle(image, (x,y), (x+w,y+h), (0, 255, 0), 2)
            x_center = int(0.5*(2*x + w))
            y_center = int(0.5*(2*y + h))
            x_left = max(int(x_center - w*0.8), 0)
            y_left = max(int(y_center - h*0.8), 0)
            x_right = min(int(x_center + w*0.8), image.shape[1])
            y_right = min(int(y_center + h*0.8), image.shape[0])
            ROI = original[y_left:y_right, x_left:x_right]
            blurriness = blur(ROI)
            blurs.append(blurriness)
#             origin = (x_center, y_right)
#             cv2.putText(image, "{}: {:.2f}".format("Blur", blurriness), origin,
#                         cv2.FONT_HERSHEY_SIMPLEX, 0.8, (0, 0, 255), 3)
#     fig = plt.figure(figsize = (10,10)) # create a 5 x 5 figure 
#     ax = fig.add_subplot(111)
#     ax.imshow(cv2.cvtColor(image, cv2.COLOR_BGR2RGB))
#     plt.show()
    if len(blurs) == 0:
        return 0
    else:
        avg_blur = np.mean(blurs)
    return avg_blur

In [7]:
def calc_distanc(folder, dia):
    if dia == 50:
        if folder[0] == 'm':
            pos = 50 - int(folder[1:])
        else:
            pos = 50 + int(folder[1:])        
    elif dia == 100:
        if folder[0] == 'm':
            pos = 40 - int(folder[1:])
        else:
            pos = 40 + int(folder[1:])         
    elif dia == 150:
        if folder[0] == 'm':
            pos = 70 - int(folder[1:])
        else:
            pos = 70 + int(folder[1:])
    elif dia == 200:
        if folder[0] == 'm':
            pos = 110 - int(folder[1:])
        else:
            pos = 110 + int(folder[1:])
    elif dia == 300:
        if folder[0] == 'm':
            pos = 40 - int(folder[1:])
        else:
            pos = 40 + int(folder[1:])
    elif dia == 400:
        if folder[0] == 'm':
            pos = 0 - int(folder[1:])
        else:
            pos = int(folder[1:])
    return pos

In [18]:
imgpathsDefocus = []
folder_list = ['D50', 'D100', 'D150', 'D200', 'D300', 'D400']
for direc in folder_list:
    print(direc)
    path_prefix = os.path.join(r"E:\Academics\DDP\Data\Defocused", direc) 
    for folder in os.listdir(os.path.join(r"E:\Academics\DDP\Data\Defocused", direc)):
        for imgname in os.listdir(os.path.join(path_prefix, folder)):
            if imgname.endswith(".tif"):
                dia = int(direc[1:])
                pos = calc_distanc(folder, dia)
                try:
                    name = str(dia) + '_' + folder + '_' + imgname.split("_")[1]
                except:
                    print(imgname)
                    print(folder)
                imgpath = os.path.join(path_prefix, folder, imgname)

                droplet_dict = {
                    'dia' : dia,
                    'pos' : pos,
                    'name' : name,
                    'path' : imgpath
                }
                imgpathsDefocus.append(droplet_dict)
print(len(imgpathsDefocus))

D50
D100
D150
D200
D300
D400
52464


In [68]:
blur_data = []
for i in tqdm(range(len(imgpathsDefocus))):
    img = imgpathsDefocus[i]
    blur_dict = {}
    blur_dict['blur'] = blur_avg(img)
    blur_dict['dia'] = img['dia']
    blur_dict['pos'] = img['pos']
    blur_data.append(blur_dict)
df = pd.DataFrame(blur_data)
df.to_csv("blur_data.csv")

100%|██████████████████████████████████████████████████████████████████████████| 52464/52464 [1:06:46<00:00, 13.09it/s]


In [70]:
df50 = df[df.dia == 50]
df100 = df[df.dia == 100]
df150 = df[df.dia == 150]
df200 = df[df.dia == 200]
df300 = df[df.dia == 300]
df400 = df[df.dia == 400]

In [78]:
fig = px.scatter(df[df.blur < 2300], x = 'pos', y = 'blur', title='Blurring vs Position: All diameters')
fig.show()
fig.write_image(r"alldia.png")

In [72]:
fig = px.scatter(df50, x = 'pos', y = 'blur', title='Blurring vs Position: 50 micron')
fig.show()
fig.write_image(r"50.png")

In [73]:
fig = px.scatter(df100, x = 'pos', y = 'blur', title='Blurring vs Position: 100 micron')
fig.show()
fig.write_image(r"100.png")

In [74]:
fig = px.scatter(df150, x = 'pos', y = 'blur', title='Blurring vs Position: 150 micron')
fig.show()
fig.write_image(r"150.png")

In [79]:
fig = px.scatter(df200[df < 2000], x = 'pos', y = 'blur', title='Blurring vs Position: 200 micron')
fig.show()
fig.write_image(r"200.png")

In [76]:
fig = px.scatter(df300, x = 'pos', y = 'blur', title='Blurring vs Position: 300 micron')
fig.show()
fig.write_image(r"300.png")

In [80]:
fig = px.scatter(df400[df > 0], x = 'pos', y = 'blur', title='Blurring vs Position: 400 micron')
fig.show()
fig.write_image(r"400.png")